In [7]:
import os
import sys
import pandas as pd

# sys.path.append(os.path.dirname(os.getcwd()))
os.chdir("..")

In [8]:
import json
json_file = open("tests/dataset/ques_ans.json")
evaluation_queries = json.load(json_file)

In [9]:
eval_df = pd.DataFrame({
    'prompt_type': [category for category in evaluation_queries for _ in evaluation_queries[category]],
    'prompt': [query['prompt'] for category in evaluation_queries.values() for query in category],
    'expected_response': [query['response'] for category in evaluation_queries.values() for query in category]
})

In [10]:
eval_df = eval_df[:10]

In [11]:
import dspy
from pydantic import BaseModel, Field

class Score(BaseModel):
    commentary: str = Field(desc="The analysis of the score")
    Score: int = Field(desc="The score")

class Scorer(dspy.Signature):
    """
    You are a code evaluating agent. You take a query and code for evaluation. 
    You need to +1 for each of these attributes in the code

    {'correct_column_names','title','Annotations', 'Aggregation used',
    'correct axis label','Plotly_white theme','Correct chart type'}

    You are provided with a {query}
    and Plotly code {code}
    You need to tell me the total score
    
    """
    query = dspy.InputField(desc="user query which includes information about data and chart they want to plot")
    code = dspy.InputField(desc="The agent generated code")
    output: Score = dspy.OutputField(desc='The score after evaluating the code')


def check_code_run(code):
    score = 0
    try:
        code = code.split('```')[1]
        exec(code)
        score += 10
        return score

    except:
        return score
    
import re

def extract_integers(text):
    return [int(num) for num in re.findall(r'\d+', text)]

def evaluating_response(code, query):
    score = 0
    scorer = dspy.Predict(Scorer)
# Feeds the code and query to the LLM for evaluation
    response = scorer(query=query, code=code)
# Parses the LLM output, your implementation may vary
    print(response)
    score+=extract_integers(response.output)[0]
    return score

In [25]:
from io import BytesIO
from agentlite.llm.LLMConfig import LLMConfig
from agentlite.llm.agent_llms import get_llm_backend
from agentlite_finance.memory.shared_memory import SharedMemory
from agentlite_finance.actions.code_generation_action import CodeGenerationAction
from agentlite_finance.actions.file_handler_action import FileHandlerAction
from agentlite_finance.actions.generic_insights_action import GenericInsightsAction
from agentlite_finance.actions.plotting_action import PlottingAction
from agentlite.logging.terminal_logger import AgentLogger
from agentlite_finance.examples.agents_example import AgentsExample
from agentlite_finance.examples.manager_example import ManagerExample
from agentlite_finance.actions.preprocessing_action import PreprocessingAction
from agentlite.commons import TaskPackage
from agentlite_finance.memory.memory_keys import FILE

llm_config_dict = {
                    "llm_name": "gpt-3.5-turbo",
                    "temperature": 0.0,
                    "max_tokens": 2000,
                    "api_key": "sk-Vo7jCT5lrwMyJ1YeqpzmYvDaS9sYF4Xt_BPLSaiOywT3BlbkFJVP2JXFoP36HSMWqWluMD88AkB7t0KHJ8j-FM0BUngA"
                    }
llm_config = LLMConfig(llm_config_dict)
llm = get_llm_backend(llm_config)

# define the logger. You can set the PROMPT_DEBUG_FLAG=True to show the actual prompt and generation for LLM
agent_logger = AgentLogger(PROMPT_DEBUG_FLAG=False) 

stock_file_path = "tests/dataset/all_stocks_5yr.csv"
stock_data_file = open(stock_file_path, "rb")

stock_data_bytesio = BytesIO(stock_data_file.read())
stock_data_bytesio.name = stock_file_path.split('/')[-1]

# Initialize agents
shared_mem = SharedMemory()
shared_mem.add(FILE, stock_data_bytesio)

file_handler_action = FileHandlerAction(shared_mem)
preprocessing_action = PreprocessingAction(shared_mem)

from agentlite_finance.agents.data_agent import DataAgent
data_agent = DataAgent(
    llm=llm,
    actions=[file_handler_action, preprocessing_action],
    shared_mem=shared_mem,
    logger=agent_logger
    )

codegeneration_action = CodeGenerationAction(shared_mem)
plotting_action = PlottingAction(shared_mem)
from agentlite_finance.agents.visualization_agent import VisualizationAgent
visualization_agent = VisualizationAgent(
    llm=llm,
    actions=[codegeneration_action, plotting_action],
    shared_mem=shared_mem,
    logger=agent_logger
    )

generic_insights_action = GenericInsightsAction(shared_mem)
from agentlite_finance.agents.generic_agent import GenericAgent
generic_agent = GenericAgent(
    llm=llm,
    actions=[generic_insights_action],
    shared_mem=shared_mem,
    logger=agent_logger
    ) 

example_task1, act_chain1 = AgentsExample().build_data_agent_example()
data_agent.add_example(task=example_task1, action_chain=act_chain1)
example_task2, act_chain2 = AgentsExample().build_visualisation_example()
visualization_agent.add_example(task=example_task2, action_chain=act_chain2)
example_task3, act_chain3 = AgentsExample().build_summary_example()
generic_agent.add_example(task=example_task3, action_chain=act_chain3)

# Manager agent
from agentlite_finance.manager.finance_data_manager import FinanceDataManagerAgent
finance_data_manager = FinanceDataManagerAgent(
    llm=llm,
    team=[
            data_agent ,visualization_agent, generic_agent                    
        ],
    logger=agent_logger
)
manager_task, manager_chain = ManagerExample().build_manager_example()
finance_data_manager.add_example(task=manager_task, action_chain=manager_chain)

summary_task, summary_chain = ManagerExample().build_manager_example_for_data_summary()
finance_data_manager.add_example(task=summary_task, action_chain=summary_chain)

#############human_template: {prompt}
#############PromptTemplate(prompt): input_variables=['prompt'] template='{prompt}'


In [26]:
import dspy
from pydantic import BaseModel, Field

class Plotly_code(BaseModel):
    commentary: str = Field(desc="The comments about the code")
    Code: str = Field(desc="The Plotly Code")

class AgentSig(dspy.Signature):
    """
    You are AI agent who uses the {query} to generate data visualizations in Plotly.
    You must give an output as code, in case there is no relevant columns, just state
    that you don't have the relevant information
    """
    query = dspy.InputField(desc="user query which includes information about data and chart they want to plot")
    code: Plotly_code = dspy.OutputField(desc="Plotly code that visualizes what the user needs according to the query & dataframe_index & styling_context")


class AI_data_viz_agent(dspy.Module):
    def __init__(self):
        super().__init__()
        self.agent = finance_data_manager
    
    def forward(self, query):
        task_pack = TaskPackage(instruction=query)
        prediction = self.agent(task_pack)
        print(prediction)
        return dspy.Prediction(code=prediction)


lm = dspy.OpenAI(model='gpt-3.5-turbo', api_key="sk-Vo7jCT5lrwMyJ1YeqpzmYvDaS9sYF4Xt_BPLSaiOywT3BlbkFJVP2JXFoP36HSMWqWluMD88AkB7t0KHJ8j-FM0BUngA")
dspy.configure(lm=lm)
agent=AI_data_viz_agent()
print(agent('What is the moving average of AAL stock?').code)

Agent DataManager receives the following TaskPackage:
[
	Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
	Instruction: What is the moving average of AAL stock?
]
Before Assign----------------Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
Instruction: What is the moving average of AAL stock?
Task Creator: 
Task Completion:active
Answer: 
Task Executor: 
Before Execute----------------Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
Instruction: What is the moving average of AAL stock?
Task Creator: 
Task Completion:active
Answer: 
Task Executor: 
====DataManager starts execution on TaskPackage 7b8e0722-de35-487f-b00c-88bb69800d5c====
During Execution----------------Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
Instruction: What is the moving average of AAL stock?
Task Creator: 
Task Completion:active
Answer: 
Task Executor: 
#############LangchainLLM(run): You are a manager agent. You can assign a task to those agents in your team. Follow your [Role], [Action_Doc], [Team_Doc] to take actions.


In [28]:
code_list =[]
for q in eval_df['prompt']:
    code_list.append(agent(q).code)
eval_df['received_response'] = code_list

eval_df['check_run'] = [check_code_run(code) for code in eval_df['received_response']]

eval_df['score'] = [evaluating_response(code,query) for code,query in zip(eval_df['received_response'],eval_df['prompt'])]

eval_df['answerable'] = [1 if x.strip().lower()!='no relevant information' else 0 for x in eval_df['expected_response']]


Agent DataManager receives the following TaskPackage:
[
	Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
	Instruction: What was the closing price of ORCL on 2014-05-19?
]
Before Assign----------------Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
Instruction: What was the closing price of ORCL on 2014-05-19?
Task Creator: 
Task Completion:active
Answer: 
Task Executor: 
Before Execute----------------Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
Instruction: What was the closing price of ORCL on 2014-05-19?
Task Creator: 
Task Completion:active
Answer: 
Task Executor: 
====DataManager starts execution on TaskPackage 7b8e0722-de35-487f-b00c-88bb69800d5c====
During Execution----------------Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
Instruction: What was the closing price of ORCL on 2014-05-19?
Task Creator: 
Task Completion:active
Answer: 
Task Executor: 
#############LangchainLLM(run): You are a manager agent. You can assign a task to those agents in your team. Follow your [Role], [Actio

In [29]:
def final_score(a,c,a_s,code):
    return a * (c + a_s)

In [30]:
class CodeJudge(dspy.Signature):
    """Judge if the response has any code"""
    response = dspy.InputField(desc="Response from AI agent")
    has_code = dspy.OutputField(desc="Does the response contain any Python code", prefix="Factual[Yes/No]:")

# A metric that calculates the final score for every predicted response
# compared with the example which contains the best response
def full_metric(example,pred, trace=None):
    if 'No relevant information' not in example.code:
        check_run = check_code_run(pred.code)
        attributes = evaluating_response(pred.code,example.query)
    else:
        check_if_code = dspy.ChainOfThought(CodeJudge)
        response = check_if_code(response=pred.code)
        if response.has_code.split('Factual[Yes/No]:')[1].strip()=='Yes':
            return 0
        else:
            return 19
        
    return check_run + attributes

zip_ = zip(eval_df['answerable'],eval_df['check_run'],eval_df['score'],eval_df['received_response'])
eval_df['total_score'] = [final_score(a,c,a_s,code) for a,c,a_s,code in zip_]

# computing the total score/total attainable score

eval_df['total_score'].sum()/(len(eval_df)*19)

0.0

In [31]:
print("Intial score: ",format(eval_df['total_score'].sum()/(len(eval_df)*19)*100, '0.2f') + "%")

Intial score:  0.00%


In [32]:
eval_df.sample(10)

prompt_type                                             prompt  \
7  Stock Performance   What was the closing price of AMP on 2015-10-14?   
2  Stock Performance  What was the closing price of ARNC on 2017-12-13?   
3  Stock Performance   What was the closing price of NBL on 2015-11-25?   
6  Stock Performance   What was the closing price of AIV on 2016-04-29?   
5  Stock Performance   What was the closing price of AAL on 2016-01-21?   
9  Stock Performance   What was the closing price of DTE on 2015-10-14?   
0  Stock Performance  What was the closing price of ORCL on 2014-05-19?   
1  Stock Performance   What was the closing price of DPS on 2014-06-24?   
4  Stock Performance  What was the closing price of ILMN on 2015-07-06?   
8  Stock Performance  What was the closing price of LRCX on 2013-02-20?   

  expected_response                                  received_response  \
7           $107.57  The closing price of AMP on October 14, 2015 w...   
2            $25.18  The closing price of ARNC on 2017-12-13 was $2...   
3            $36.94  The closing price of NBL on 2015-11-25 was $32...   
6            $40.06  The closing price of AIV on April 29, 2016 was...   
5            $39.79  The closing price of AAL on 2016-01-21 was $40...   
9            $81.76  The closing price of DTE on October 14, 2015 w...   
0            $42.16  The closing price of ORCL on 2014-05-19 was $4...   
1            $58.56  The closing price of DPS on 2014-06-24 was $58...   
4           $220.51  The closing price of ILMN on July 6, 2015 was ...   
8            $41.96  The closing price of LRCX on 2013-02-20 was $3...   

   check_run  score  answerable  total_score  
7          0      0           1            0  
2          0      0           1            0  
3          0      0           1            0  
6          0      0           1            0  
5          0      0           1            0  
9          0      0           1            0  
0          0      0           1            0  
1          0      0           1            0  
4          0      0           1            0  
8          0      0           1            0

In [33]:
# Defined a new signature for the code improver agent
class Improver(dspy.Signature):
    """
    You are a code-improving agent. You take code and commentary and output improved code improvement. 
    You need to take the code and commentary and output Plotly code that would have a perfect score.

    These were the 9 attributes the code was judged on, +1 for every correct answer
    {'correct_column_names','title','Annotations','Aggregation used','correct axis label',
    'Plotly_white theme','Correct chart type',}

    This is the format you need to follow
    code: {code}
    commentary:{commentary}
    improved_code: The output that would score 9
    """
    code = dspy.InputField(desc="The code you need to improve")
    commentary = dspy.InputField(desc="The commentary on the code provided by evaluation agent")
    improved_code = dspy.OutputField(desc="The improved code that would get a perfect score as per commentary")

improver = dspy.ChainOfThought(Improver)
# You can use the scorer module defined earlier to verify the code meets
# the criteria you want
scorer = dspy.ChainOfThought(Scorer)

In [35]:
# Creating a judge signature
class CodeJudge(dspy.Signature):
    """Judge if the response has any code"""
    response = dspy.InputField(desc="Response from AI agent")
    has_code = dspy.OutputField(desc="Does the response contain any Python code", prefix="Factual[Yes/No]:")

# A metric that calculates the final score for every predicted response
# compared with the example which contains the best response
def full_metric(example,pred, trace=None):
    if 'No relevant information' not in example.code:
        check_run = check_code_run(pred.code)
        attributes = evaluating_response(pred.code,example.query)
    else:
        check_if_code = dspy.ChainOfThought(CodeJudge)
        response = check_if_code(response=pred.code)
        if response.has_code.split('Factual[Yes/No]:')[1].strip()=='Yes':
            return 0
        else:
            return 19
    print(check_run + attributes)    
    return check_run + attributes
# Formating the query,code pair as DSPy Example    
trainset = [dspy.Example(query=q, code=c).with_inputs('query') for q,c in zip(eval_df['prompt'],eval_df['expected_response'])]

In [36]:
len(trainset)

10

In [37]:
from dspy.teleprompt import BootstrapFewShotWithRandomSearch

# Set up the optimizer: we want to "bootstrap" (i.e., self-generate) 8-shot examples of your program's steps.
# The optimizer will repeat this 10 times (plus some initial attempts) before selecting its best attempt on the devset.
config = dict(max_bootstrapped_demos=2, max_labeled_demos=2, num_candidate_programs=3, num_threads=4)

# Few Shot With Random Search (oversimplified) works by using the LLM to generate examples,
# Then it tests how well those examples do on evaluation
# After multiple iterations you will have good examples for your training set
teleprompter = BootstrapFewShotWithRandomSearch(metric=full_metric, **config)
optimized_agent = teleprompter.compile(agent, trainset=trainset)

Going to sample between 1 and 2 traces per predictor.
Will attempt to bootstrap 3 candidate sets.
Failed to deep copy attribute 'agent' of AI_data_viz_agent, falling back to shallow copy or reference copy.
Agent DataManager receives the following TaskPackage:
[
	Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
	Instruction: What was the closing price of ORCL on 2014-05-19?
]
Agent DataManager receives the following TaskPackage:
[
	Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
	Instruction: What was the closing price of DPS on 2014-06-24?
]
Agent DataManager receives the following TaskPackage:
[
	Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
	Instruction: What was the closing price of ARNC on 2017-12-13?
]
Agent DataManager receives the following TaskPackage:
[
	Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
	Instruction: What was the closing price of NBL on 2015-11-25?
]
Before Assign----------------Task ID: 7b8e0722-de35-487f-b00c-88bb69800d5c
Instruction: What was the closing price of AR

  0%|          | 0/10 [00:00<?, ?it/s]

INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
#############LangchainLLM(result): DataAgent[{"Task": "Use FileHandler to load the data and then Preprocess it."}]
-->StringParseAction=DataAgent[{"Task": "Use FileHandler to load the data and then Preprocess it."}]
---------->Action_Type=DataAgent
---------->arguments={"Task": "Use FileHandler to load the data and then Preprocess it."}
-->StringParseAction=DataAgent[{"Task": "Use FileHandler to load the data and then Preprocess it."}],Argument={'Task': 'Use FileHandler to load the data and then Preprocess it.'}
Agent DataManager takes 0-step Action:
{
	name: DataAgent
	params: {'Task': 'Use FileHandler to load the data and then Preprocess it.'}
}
##

Average Metric: 0 / 1  (0.0):  10%|█         | 1/10 [00:09<01:29,  9.89s/it]

#############LangchainLLM(result): Finish[{"response": "The closing price of ARNC on 2017-12-13 was $24.56."}]
-->StringParseAction=Finish[{"response": "The closing price of ARNC on 2017-12-13 was $24.56."}]
---------->Action_Type=Finish
---------->arguments={"response": "The closing price of ARNC on 2017-12-13 was $24.56."}
-->StringParseAction=Finish[{"response": "The closing price of ARNC on 2017-12-13 was $24.56."}],Argument={'response': 'The closing price of ARNC on 2017-12-13 was $24.56.'}
Agent DataManager takes 1-step Action:
{
	name: Finish
	params: {'response': 'The closing price of ARNC on 2017-12-13 was $24.56.'}
}
Before Forward----------------name='Finish' desc=None params={'response': 'The closing price of ARNC on 2017-12-13 was $24.56.'}
Observation: The closing price of ARNC on 2017-12-13 was $24.56.
=========DataManager finish execution. TaskPackage[ID:7b8e0722-de35-487f-b00c-88bb69800d5c] status:
[
	completion: completed
	answer: The closing price of ARNC on 2017-12-

...

#############LangchainLLM(result): Finish[{"response": "The closing price of AIV on April 29, 2016 was $40.06."}]
-->StringParseAction=Finish[{"response": "The closing price of AIV on April 29, 2016 was $40.06."}]
---------->Action_Type=Finish
---------->arguments={"response": "The closing price of AIV on April 29, 2016 was $40.06."}
-->StringParseAction=Finish[{"response": "The closing price of AIV on April 29, 2016 was $40.06."}],Argument={'response': 'The closing price of AIV on April 29, 2016 was $40.06.'}
Agent DataManager takes 2-step Action:
{
	name: Finish
	params: {'response': 'The closing price of AIV on April 29, 2016 was $40.06.'}
}
Before Forward----------------name='Finish' desc=None params={'response': 'The closing price of AIV on April 29, 2016 was $40.06.'}
Observation: The closing price of AIV on April 29, 2016 was $40.06.
=========DataManager finish execution. TaskPackage[ID:7b8e0722-de35-487f-b00c-88bb69800d5c] status:
[
	completion: completed
	answer: The closing p

Average Metric: 7.0 / 9  (77.8):  90%|█████████ | 9/10 [00:29<00:02,  2.80s/it]

#############LangchainLLM(result): Finish[{"response": "The closing price of AMP on 2015-10-14 was $107.57."}]
-->StringParseAction=Finish[{"response": "The closing price of AMP on 2015-10-14 was $107.57."}]
---------->Action_Type=Finish
---------->arguments={"response": "The closing price of AMP on 2015-10-14 was $107.57."}
-->StringParseAction=Finish[{"response": "The closing price of AMP on 2015-10-14 was $107.57."}],Argument={'response': 'The closing price of AMP on 2015-10-14 was $107.57.'}
Agent DataManager takes 2-step Action:
{
	name: Finish
	params: {'response': 'The closing price of AMP on 2015-10-14 was $107.57.'}
}
Before Forward----------------name='Finish' desc=None params={'response': 'The closing price of AMP on 2015-10-14 was $107.57.'}
Observation: The closing price of AMP on 2015-10-14 was $107.57.
=========DataManager finish execution. TaskPackage[ID:7b8e0722-de35-487f-b00c-88bb69800d5c] status:
[
	completion: completed
	answer: The closing price of AMP on 2015-10-1

Average Metric: 7.0 / 10  (70.0): 100%|██████████| 10/10 [00:31<00:00,  3.17s/it]

Prediction(
    output='Output: 0'
)
0
INFO:dspy.evaluate.evaluate:2024-10-08T18:49:06.595256Z [info     ] Average Metric: 7.0 / 10 (70.0%) [dspy.evaluate.evaluate] filename=evaluate.py lineno=218
2024-10-08T18:49:06.595256Z [info     ] Average Metric: 7.0 / 10 (70.0%) [dspy.evaluate.evaluate] filename=evaluate.py lineno=218
New best score: 70.0 for seed 2
Scores so far: [0.0, 0.0, 0.0, 0.0, 0.0, 70.0]
Best score so far: 70.0
6 candidate programs found.


In [38]:
lm.inspect_history(n=1)




You are a code evaluating agent. You take a query and code for evaluation. 
You need to +1 for each of these attributes in the code

{'correct_column_names','title','Annotations', 'Aggregation used',
'correct axis label','Plotly_white theme','Correct chart type'}

You are provided with a {query}
and Plotly code {code}
You need to tell me the total score

---

Follow the following format.

Query: user query which includes information about data and chart they want to plot
Code: The agent generated code
Output: The score after evaluating the code

---

Query: What was the closing price of DTE on 2015-10-14?
Code: Data loaded and preprocessed successfully. Ready for further analysis.
Output: Output: 0





"\n\n\nYou are a code evaluating agent. You take a query and code for evaluation. \nYou need to +1 for each of these attributes in the code\n\n{'correct_column_names','title','Annotations', 'Aggregation used',\n'correct axis label','Plotly_white theme','Correct chart type'}\n\nYou are provided with a {query}\nand Plotly code {code}\nYou need to tell me the total score\n\n---\n\nFollow the following format.\n\nQuery: user query which includes information about data and chart they want to plot\nCode: The agent generated code\nOutput: The score after evaluating the code\n\n---\n\nQuery: What was the closing price of DTE on 2015-10-14?\nCode: Data loaded and preprocessed successfully. Ready for further analysis.\nOutput:\x1b Output: 0\x1b\n\n\n"

In [39]:
print(trainset[:25])

[Example({'query': 'What was the closing price of ORCL on 2014-05-19?', 'code': '$42.16'}) (input_keys={'query'}), Example({'query': 'What was the closing price of DPS on 2014-06-24?', 'code': '$58.56'}) (input_keys={'query'}), Example({'query': 'What was the closing price of ARNC on 2017-12-13?', 'code': '$25.18'}) (input_keys={'query'}), Example({'query': 'What was the closing price of NBL on 2015-11-25?', 'code': '$36.94'}) (input_keys={'query'}), Example({'query': 'What was the closing price of ILMN on 2015-07-06?', 'code': '$220.51'}) (input_keys={'query'}), Example({'query': 'What was the closing price of AAL on 2016-01-21?', 'code': '$39.79'}) (input_keys={'query'}), Example({'query': 'What was the closing price of AIV on 2016-04-29?', 'code': '$40.06'}) (input_keys={'query'}), Example({'query': 'What was the closing price of AMP on 2015-10-14?', 'code': '$107.57'}) (input_keys={'query'}), Example({'query': 'What was the closing price of LRCX on 2013-02-20?', 'code': '$41.96'}) 

In [40]:
print(full_metric)

<function full_metric at 0x142e3a9e0>


In [41]:
from dspy.teleprompt import COPRO

# Initializing COPRO with our designed metric and breadth tells 
# how many optimizations to try
teleprompter = COPRO(
    metric=full_metric,
    verbose=True,breadth=5
)
# num_threads is how many instances it opens with the LLM
# be careful as opening too many would exhaust your API and may charge you
kwargs = dict(num_threads=1, display_progress=True, display_table=0) # Used in Evaluate class in the optimization process

# compiling our program
compiled_prompt_opt = teleprompter.compile(agent, trainset=trainset[:10], eval_kwargs=kwargs)
# saving it to review later
compiled_prompt_opt.save('COPRO_agent.json')

Failed to deep copy attribute 'agent' of AI_data_viz_agent, falling back to shallow copy or reference copy.
Failed to deep copy attribute 'agent' of AI_data_viz_agent, falling back to shallow copy or reference copy.
INFO:dspy.teleprompt.copro_optimizer:2024-10-08T18:55:17.133453Z [info     ] Iteration Depth: 1/3.          [dspy.teleprompt.copro_optimizer] filename=copro_optimizer.py lineno=191
2024-10-08T18:55:17.133453Z [info     ] Iteration Depth: 1/3.          [dspy.teleprompt.copro_optimizer] filename=copro_optimizer.py lineno=191
INFO:dspy.teleprompt.copro_optimizer:2024-10-08T18:55:17.147691Z [info     ] Iteration Depth: 2/3.          [dspy.teleprompt.copro_optimizer] filename=copro_optimizer.py lineno=191
2024-10-08T18:55:17.147691Z [info     ] Iteration Depth: 2/3.          [dspy.teleprompt.copro_optimizer] filename=copro_optimizer.py lineno=191
INFO:dspy.teleprompt.copro_optimizer:2024-10-08T18:55:17.155331Z [info     ] Iteration Depth: 3/3.          [dspy.teleprompt.copro_opt

IndexError: list index out of range

In [42]:
#you can check the candidate program by using the __dict__ inside every DSPy Program
compiled_prompt_opt.__dict__

NameError: name 'compiled_prompt_opt' is not defined